In [2]:
import pandas as pd
import re
import string
import time

from collections import Counter, defaultdict

from needleman_wunsch import needleman_wunsch

from fuzzywuzzy import fuzz

from operator import itemgetter

pd.set_option('display.max_rows', 1000)

In [3]:
df = pd.read_excel('data/dataYiddish/nli/potsdam1.xlsx', header=None, names=['id', 'title', 'trans'])

In [4]:
df.sample()

id                                              title  \
2939  990012625120205171  $$aדיא פרוי און דער סאציאליזמוס :$$bdie Frau u...   

                                                  trans  
2939  $$aDi froy un der Sotsyalizmus = Die frau und ...

In [7]:
len(df)

8972

In [5]:
df['title_'] = df.title.apply(lambda x: re.sub('\$\$[a-z]', '', x))
df['trans_'] = df.trans.apply(lambda x: re.sub('\$\$[a-z]', '', x))

In [6]:
df.sample()

id                                           title  \
39  990013429430205171  $$aראסע :$$bלינטשעריי און אנדערע דערציילונגען.   

                                           trans  \
39  $$aRase, linṭsheray un andere dertseylungen   

                                      title_  \
39  ראסע :לינטשעריי און אנדערע דערציילונגען.   

                                       trans_  
39  Rase, linṭsheray un andere dertseylungen

### the hyphenation is inconsistent, so I replace all hyphens with a space

In [39]:
#df['title__'] = df.title_.apply(lambda x: re.sub('\-', ' ', x))
#df['trans__'] = df.trans_.apply(lambda x: re.sub('\-', ' ', x))

In [7]:
df['title_'] = df.title_.apply(lambda x: re.sub('[^\u0590-\u05fe \-]+', '', x))
df['trans_'] = df.trans_.apply(lambda x: re.sub('[^\w \-]+', '', x))

### diacritics in romanization are not preserved, they seem to be encoded in a weird way (show up under different letters)--so maybe it's ok?

In [8]:
letterpairs = [(pair[0][0], pair[1][0].lower()) for pair in zip(df.title_.values, df.trans_.values)]

In [9]:
letterdict = defaultdict(str)

for tup in Counter(letterpairs).most_common()[::-1]:
    letterdict[tup[0][0]] = tup[0][1]

In [10]:
letterdict

defaultdict(str,
            {'צ': 't',
             'ו': 'v',
             'ע': 'e',
             'ב': 'b',
             'ה': 'h',
             'נ': 'n',
             'י': 'y',
             'ק': 'k',
             'ל': 'l',
             ' ': '1',
             'ג': 'g',
             'א': 'a',
             'ד': 'd',
             'ז': 'z',
             'מ': 'm',
             'פ': 'f',
             'ת': 't',
             'כ': 'k',
             'ש': 's',
             'ח': 'h',
             'ס': 's',
             'ט': 't',
             'ר': 'r'})

In [ ]:
letterdict['כ'] = 'kh'
letterdict['ך'] = 'kh'
letterdict['צ'] = 'ts'
letterdict['ץ'] = 'ts'
letterdict['ש'] = 'sh'
letterdict['-'] = '-'
letterdict['ע'] = 'e'
letterdict['ן'] = 'n'
letterdict['ם'] = 'm'
letterdict['ף'] = 'f'
letterdict[' '] = ' '
#letterdict['א'] = 'a'
#letterdict['י'] = 'i'
#letterdict['ײ'] = 'ey'
#letterdict['־'] = '-'

for num in range(10):
    letterdict[str(num)] = str(num)
    
for punct in string.punctuation:
    letterdict[punct] = punct

In [12]:
wordlist = []
worddict = {'אין': 'in', 'און': 'un'}

for h, l in zip(df.title_, df.trans_):
    matches = defaultdict(lambda: ('', 0),)
    for i, word in enumerate(h.split()):
        if word in worddict.keys():
            pseudotrans = worddict[word]
        else:
            pseudotrans = ''.join([letterdict[letter] for letter in word]) 
        ratios = []
        for j, trans in enumerate(l.split()):
            ratio = fuzz.ratio(pseudotrans.lower(), trans.lower()) - abs(i-j)
            ratios.append((trans, pseudotrans, ratio))
        maxratio = max(ratios, key=itemgetter(2))
        print(maxratio)
        if maxratio[2] >= 50:
            if matches[maxratio[0]][1] >= maxratio[2]:
                pass
            elif matches[maxratio[0]][1] < maxratio[2]:
                matches[maxratio[0]] = (word, maxratio[2])
    for key, val in matches.items():
        wordlist.append((val[0], key))
        print(val[0], key)
    print()

('Geklibene', 'geklybene', 89)
('shriftn', 'shryftn', 86)
('shriftn', 'fvn', 39)
('shriftn', 'mshh', 34)
('shriftn', 'fryylykhavv', 8)
געקליבענע Geklibene
שריפטן shriftn

('Dem', 'dem', 100)
('Natsis', 'natsys', 83)
('Yidishe', 'yydyshe', 71)
('tokhter', 'takhter', 86)
('dray', 'a', 38)
('lebns-bild', 'lebens-byld', 85)
('in', 'in', 99)
('dray', 'dryy', 74)
('aktn', 'aktn', 99)
('mit', 'myt', 66)
('prolog', 'fralag', 49)
('un', 'un', 99)
('epilog', 'efylag', 49)
דעם Dem
נאציס Natsis
יידישע Yidishe
טאכטער tokhter
לעבענס-בילד lebns-bild
אין in
דריי dray
אקטן aktn
מיט mit
און un

('Farnakhtengold', 'farnakhtengald', 93)
פארנאכטענגאלד Farnakhtengold

('Undzere', 'avndzere', 80)
('politishe', 'falytyshe', 56)
('tsiln', 'tsyln', 80)
('in', 'in', 100)
('Erets-Yisroʼel', 'arts-yshral', 64)
('un', 'un', 100)
('di', 'dy', 50)
('Idish-Arabishe', 'aydysh-arabyshe', 76)
('batsiungen', 'batsyavngen', 76)
('Idish-Arabishe', 'brvkh', 19)
('batsiungen', 'tsvkerman', 40)
אונדזערע Undzere
פאליטישע politi

('tsayt', 'tsyyt', 80)
('on', 'khvan', 27)
('tsayt', 'ferkavvytsh', 36)
('tsayt', 'svsana', 33)
('far', 'franka', 36)
('far', 'sesar', 41)
('far', 'falata', 34)
('tsayt', 'ayberzetsvng', 28)
('tsayt', 'ayydl', 32)
('magiker', 'myykler', 39)
די Di
פינף finf
מאגיקער magiker
פון fun
נאטרע-דאם Notre-Dam
הונדערט hundert
יאר yor
פאר far
אויגנבליק oygnblik
אן on
צייט tsayt

('Olgin', 'algyn', 60)
('dermont', 'dermant', 86)
('unz', 'avnz', 57)
('Olgin', 'fartsyykhenvngen', 16)
('unz', 'fvn', 31)
('Olgin', 'shlmh', 15)
('dermont', 'davvydman', 33)
אלגין Olgin
דערמאנט dermont
אונז unz

('Mayne', 'myyne', 80)
('lider', 'lyder', 80)
('zaynen', 'zyynen', 83)
('nit', 'nyt', 67)
('tsum', 'tsvm', 75)
('zingen', 'zyngen', 83)
('nit', 'fvn', 30)
('Mayne', 'yekb', 37)
('tsum', 'tshekhanavvsky', 18)
מיינע Mayne
לידער lider
זיינען zaynen
ניט nit
צום tsum
זינגען zingen

('Mit', 'myt', 67)
('der', 'der', 100)
('dratve', 'dratvve', 92)
('-', '-', 100)
('a', 'a', 100)
('dertseylung', 'tsy', 42)
('dertseylung',

('Tov', 'zytsvng', 35)
('vegen', 'fvn', 40)
('torat', 'agvdt', 30)
('Shem', 'hadmvrym', 24)
('vegen', 'in', 16)
('Tov', 'nyv', 23)
('Moroko', 'yark', 24)
('Shem', 'hy', 20)
('Baal', 'alvl', 35)
('Shem', 'tshyd', 29)
('Shem', 'shnyavr', 20)
('Shem', 'zlmn', 8)
('Fraynkraykh', 'shnyavrsahn', 12)
וועגען Vegen
פריינקרייך Fraynkraykh
וועגען vegen
מאראקא Moroko
תורת torat
הבעל Baal
שם Shem
טוב Tov

('Ufshtayg', 'avfshtyyg', 71)
('Ufshtayg', 'd', -1)
('Ufshtayg', 'bagen', 29)
('Ufshtayg', 'grshvn', 26)
('Ufshtayg', 'dvah', 13)
אופשטייג Ufshtayg

('Der', 'der', 100)
('mentsh', 'mentsh', 100)
('dertseylungen', 'dertsyylvngen', 85)
דער Der
מענטש mentsh
דערציילונגען dertseylungen

('Verk', 'vverk', 89)
('Tse', 'tse', 100)
ווערק Verk
צע Tse

('Literatur', 'lyteratvr', 78)
('un', 'un', 100)
('shprakh', 'shfrakh', 86)
('fun', 'fvn', 67)
('der', 'der', 100)
('Idisher', 'aydysher', 67)
('gas', 'gas', 100)
ליטעראטור Literatur
און un
שפראך shprakh
פון fun
דער der
אידישער Idisher
גאס gas

('Fertsik', 'fe

('Vili', 'yefrvykyn', 9)

('vi', 'vvy', 38)
('mʼvert', 'mvvert', 81)
('vos', 'vvas', 55)
('men', 'men', 98)
('iz', 'ayz', 38)
('homo', 'frydrykh', 13)
('men', 'nytshe', 21)
('vos', 'yydysh', 19)
('iz', '-', -2)
('men', 'n', 46)
('mʼvert', 'ayybeshyts', 18)
מווערט mʼvert
וואס vos
מען men

('Geboy', 'gebvy', 80)
('kharakter', 'kharakter', 100)
('un', 'un', 100)
('oyfshtayg', 'avyfshtyyg', 74)
('fun', 'fvn', 67)
('Histadrut', 'hstdrvt', 75)
('vos', 'vvas', 57)
('di', 'dy', 50)
('Histadrut', 'hstdrvt', 75)
('fodert', 'fadert', 83)
('funem', 'fvnem', 80)
('arbeter', 'arbeter', 100)
('un', 'un', 100)
('vos', 'vvas', 57)
('di', 'dy', 50)
('Histadrut', 'hstdrvt', 75)
('git', 'gvt', 67)
('dem', 'dem', 100)
('arbeter', 'arbeter', 100)
('dem', 'mlkh', 27)
('un', 'nvy', 32)
('Histadrut', 'nyyshtadt', 50)
געבוי Geboy
כאראקטער kharakter
און un
אויפשטייג oyfshtayg
פון fun
הסתדרות Histadrut
וואס vos
די di
פאדערט fodert
פונעם funem
ארבעטער arbeter
גוט git
דעם dem

('Oyf', 'avyf', 57)
('zaytike', 'zyyty

ראמאן roman

('Dertseylungen', 'dertsyylvngen', 85)
('Dertseylungen', 'a', -1)
('Dertseylungen', 'ryyzen', 40)
דערציילונגען Dertseylungen

('Geld', 'geld', 100)
('liebe', 'lyebe', 80)
('un', 'un', 100)
('shande', 'shande', 100)
('pyese', 'fyese', 80)
('in', 'in', 100)
('aktn', 'akten', 88)
('pyese', 'ytshk', 37)
('aktn', 'zalatarevvsky', 23)
געלד Geld
ליעבע liebe
און un
שאנדע shande
פיעסע pyese
אין in
אקטען aktn

('bay', 'byne', 56)
('Bine-maskes', 'maskes', 70)
('bay', 'byy', 66)
('Katsetler', 'katsetler', 99)
('Yidish', 'yydysh', 66)
('teater', 'teater', 99)
('nokhn', 'nakhn', 79)
('hurbn', 'hvrbn', 79)
('hurbn', 'h', 31)
('teater', 'ferlmvter', 48)
ביי bay
מאסקעס Bine-maskes
קאצעטלער Katsetler
יידיש Yidish
טעאטער teater
נאכן nokhn
חורבן hurbn

('Mayses', 'meshyvt', 46)
('un', 'un', 100)
('monologn', 'manalagn', 62)
און un
מאנאלאגן monologn

('Di', 'dy', 50)
('teorye', 'tearye', 83)
('un', 'un', 100)
('praktik', 'fraktyk', 71)
('fun', 'fvn', 67)
('anarkhizm', 'anarkhyzm', 89)
('gekli

...

('fayer', 'ayn', 48)
('rizikn', 'ryzykn', 67)
('fayer', 'fyyer', 80)
('fayer', 'ezra', 43)
('fayer', 'fynynberg', 55)
ריזיקנ rizikn
פייער fayer

('Di', 'dy', 50)
('helden', 'helden', 100)
('fun', 'fvn', 67)
('Yerusholaim', 'yrvshlym', 63)
('a', 'a', 100)
('historisher', 'hystarysher', 73)
('roman', 'raman', 80)
('nokh', 'nakh', 75)
('Daniel', 'dnyal', 55)
('Mordovtsev', 'mardavvtsevv', 73)
('Mordovtsev', 'bearbyytet', 29)
('nokh', 'dvrkh', 40)
('roman', 'my', 23)
('Mordovtsev', 'fryyd', 23)
די Di
העלדען helden
פון fun
ירושלים Yerusholaim
א a
היסטארישער historisher
ראמאן roman
נאך nokh
דניאל Daniel
מארדאווצעוו Mordovtsev

('Yihes', 'yyhvs', 60)
('fun', 'fvn', 67)
('lid', 'lyd', 67)
('lekoved', 'lkhbvd', 62)
('Avraham', 'abrhm', 67)
('Sutskever', 'svtskevver', 84)
('Avraham', 'merkht', 29)
('lid', 'db', 35)
('lid', 'sdn', 27)
('Avraham', 'vahrym', 57)
ייחוס Yihes
פון fun
ליד lid
לכבוד lekoved
אברהם Avraham
סוצקעווער Sutskever

('Eli', 'aly', 33)
('Kohen', 'khhn', 67)
('undzer', 'avndzer'

('far', 'far', 100)
('gezuntheyt', 'gezvnthyyt', 80)
('geshribn', 'geshrybn', 88)
('vi', 'vvy', 40)
('tsu', 'tsv', 67)
('balansirn', 'balansyrn', 89)
('natirlekhe', 'natyrlekhe', 90)
('vegetarishe', 'vvegetaryshe', 87)
('esens', 'esns', 89)
('natirlekhe', 'nakh', 54)
('geshribn', 'der', 28)
('natirlekhe', 'vvysnshaftlykher', 49)
('vegetarishe', 'metade', 42)
('vi', 'fvn', 30)
('balansirn', 'lyne', 22)
('balansirn', 'bravn', 33)
קאך-בוך Kokh-bukh
פאר far
געזונטהייט gezuntheyt
געשריבן geshribn
צו tsu
באלאנסירן balansirn
נאטירלעכע natirlekhe
וועגעטארישע vegetarishe
עסנס esens

('Yehoash', 'yhvash', 77)
('zikorn', 'zkhrvn', 67)
('albom', 'albvm', 80)
('tsum', 'tsvm', 75)
('shloyshim', 'shlshym', 75)
('troyer', 'trvyer', 83)
('ovnt', 'avvnt', 67)
יהואש Yehoash
זכרון zikorn
אלבום albom
צום tsum
שלשים shloyshim
טרויער troyer
אוונט ovnt

('Fun', 'fvn', 67)
('mayn', 'myyn', 75)
('brunem', 'brvnes', 67)
('Fun', 'fvn', 64)
('brunem', 'raze', 38)
('brunem', 'kredytar', 26)
פון Fun
מיין mayn
ברונעס

ציוניסטישע tsienistishe
באוועגונג bavegung
אין in
מעקסיקע Meksike
פראבלעמען problemen

('Di', 'dy', 50)
('shule', 'shvle', 80)
('fun', 'fvn', 67)
('der', 'der', 100)
('tsukunft', 'tsvkvnft', 75)
('shule', 'ellen', 36)
('der', 'key', 30)
('der', 'ayberz', 40)
('der', 'dvrkh', 45)
('tsukunft', 'y', -5)
('shule', 'galdshmydt', 18)
די Di
שולע shule
פון fun
דער der
צוקונפט tsukunft

('Mi-maamakim', 'mmemkym', 56)
('Fun', 'fvn', 67)
('di', 'dy', 50)
('tifenishn', 'tyfenyshn', 78)
ממעמקים Mi-maamakim
פון Fun
די di
טיפענישן tifenishn

('A', 'a', 100)
('shtetl', 'shtetl', 100)
('in', 'in', 100)
('Moldove', 'maldavve', 67)
('Moldove', 'b', -1)
('Moldove', 'vvylner', 27)
א A
שטעטל shtetl
אין in
מאלדאווע Moldove

('In', 'in', 100)
('onhoyb', 'anhvyb', 67)
('artiklen', 'artyklen', 88)
('zikhroynes', 'zkhrvnvt', 56)
('artiklen', 'zrbbl', 29)
אין In
אנהויב onhoyb
ארטיקלען artiklen
זכרונות zikhroynes

('Unzer', 'avnzer', 73)
('ring', 'ryng', 75)
('a', 'a', 100)
('geshikhte', 'geshykhte', 89)
('fun', '

דער Der
מענטש mentsh
און un
זיין zayn
גורל goyrl
ראמאן roman

('Yidisher', 'yydysher', 75)
('vidershtand', 'vvydershtand', 87)
('in', 'in', 100)
('Natsi-okupirtn', 'natsy-akvfyrtn', 64)
('Poyln', 'fvyln', 60)
('Poyln', 'yy', 28)
('Natsi-okupirtn', 'karts', 29)
('vidershtand', 'vv', 9)
('Poyln', 'yablansky', 39)
('vidershtand', 'redagyrt', 24)
('Natsi-okupirtn', '-', 6)
('Poyln', 'm', -7)
('Natsi-okupirtn', 'zaltsman', 27)
יידישער Yidisher
ווידערשטאנד vidershtand
אין in
נאצי-אקופירטן Natsi-okupirtn
פוילן Poyln

('Di', 'dy', 50)
('naye', 'nyye', 75)
('Iidishe', 'aydyshe', 57)
('shul', 'shvl', 75)
די Di
נייע naye
אידישע Iidishe
שול shul

('A', 'a', 100)
('rayze', 'ryyze', 80)
('iber', 'ayber', 67)
('Tsentral', 'tsentral', 100)
('un', 'un', 100)
('Dorim', 'drvm', 67)
('Amerike', 'ameryka', 71)
א A
רייזע rayze
איבער iber
צענטראל Tsentral
און un
דרום Dorim
אמעריקא Amerike

('In', 'in', 100)
('di', 'dy', 50)
('negel', 'negel', 100)
('fun', 'fvn', 67)
('krieg', 'kryeg', 80)
('fun', 'fvn', 65)


('Divre', 'dbry', 44)
('heyn', 'hn', 67)
('veseykhl', 'vshkhl', 71)
('glaykhvertlekh', 'glyykhvvertlekh', 90)
('un', 'un', 100)
('anekdoten', 'anekdaten', 89)
('anekdoten', 'tsvnvyf-geklyben', 39)
('un', 'fvn', 40)
('amolige', 'alte', 54)
('un', 'un', 99)
('ernste', 'nyye', 36)
('sharfe', 'sfrym', 31)
('un', 'un', 99)
('glaykhvertlekh', 'bykher', 40)
('ernste', '-', 0)
('un', 'un', 99)
('hayntige', 'gants', 41)
('ernste', 'bazvnders', 37)
('un', 'fvn', 38)
('ernste', 'madernem', 52)
('veltlekhe', 'leben', 40)
('un', 'fvn', 35)
('Idishe', 'grshm', 29)
('Idishe', 'bader', 28)
חן heyn
ושכל veseykhl
גלייכווערטלעך glaykhvertlekh
און un
אנעקדאטען anekdoten
אלטע amolige
מאדערנעם ernste

('Agodes', 'agdvt', 55)
('lernbukh', 'lernbvkh', 88)
('fun', 'fvn', 67)
('Hebreyish', 'hebreaysh', 89)
('far', 'far', 100)
('Yidishe', 'yydyshe', 71)
('shuln', 'shvln', 80)
('shuln', 'l', 32)
('Hebreyish', 'bayan', 24)
אגדות Agodes
לערנבוך lernbukh
פון fun
העברעאיש Hebreyish
פאר far
יידישע Yidishe
שולן shuln



In [14]:
len(wordlist)

45488

In [15]:
unique_wordlist = list(set(wordlist))
len(unique_wordlist)

12173

In [19]:
pair_df = pd.DataFrame({'yiddish': [tup[0] for tup in wordlist], 'translit': [tup[1] for tup in wordlist]})

In [20]:
pair_df.groupby(['yiddish', 'translit']).size().head(1000)

yiddish               translit               
-                     -                            17
                      --                            8
                      Z-1                           1
-אן                   3-tn                          1
-אפאריזמען            afarizmen                     1
-ביבליאגראפיע         bibliografye                  1
-געשיכטעס             geshikhtes                    1
-דעצעמבער             1942-Detsember                1
-טון                  19tn                          1
-טן                   16tn                          1
                      1848-tn                       1
                      1850-tn                       1
                      20-tn                         2
                      25-tn                         1
                      27-tn                         1
                      2tn                           1
                      30-ten                        1
                      31tn          

In [21]:
pair_df['source'] = 'nli'

In [22]:
len(pair_df), len(pair_df.drop_duplicates())

(45488, 12173)

In [23]:
pair_df.drop_duplicates().to_csv('data/processed-parallel/nli.csv', index=False)